# XGB Classifier with Wrapper-Based FS

Steven Sison | March 9, 2024

## Description

This document will be used to train a model using the reduced feature set obtain by using the wrapper-based method, forward feature selection. The model will be evaluated in terms of the usual metrics (accuracy, precision, F1-score, recall) as well as the training time. The model will also be stored for future evaluation purposes.

## Training the Model

### Preliminaries

#### 1. Loading the Dataset

In [1]:
import pandas as pd                     # For data transformation
import numpy as numpy                   # For scientific calculations
import seaborn as sns                   # For data visualizations
import matplotlib.pyplot as plt         # For plotting
import plotly.graph_objects as go       # For plotting
from sklearn.model_selection import train_test_split, cross_val_score, cross_val_predict
from sklearn.metrics import accuracy_score, recall_score, precision_score, f1_score, classification_report
from sklearn.metrics import confusion_matrix, classification_report, accuracy_score, ConfusionMatrixDisplay
from xgboost import XGBClassifier, DMatrix, train
from sklearn.pipeline import Pipeline
import time
from datetime import datetime
import joblib
import os

dataset = pd.read_csv("../../../02_feature-engineering/final-datasets/binary_new_Bacud_unbalanced_lexical.csv")      # Loading the dataset

dataset.head()



url_type  url_length  url_ip_in_domain  url_domain_entropy  \
0         1          16                 0            3.169925   
1         0          35                 0            2.807355   
2         0          31                 0            2.921928   
3         1          88                 0            2.896292   
4         1         235                 0            3.405822   

   url_is_digits_in_domain  url_query_length  url_number_of_parameters  \
0                        0                 0                         0   
1                        1                 0                         0   
2                        0                 0                         0   
3                        0                49                         4   
4                        0               194                         3   

   url_number_of_digits  url_string_entropy  url_is_https  ...  \
0                     0            3.375000             0  ...   
1                     1            4.079143             0  ...   
2                     1            3.708093             0  ...   
3                     7            4.660343             0  ...   
4                    22            4.980518             0  ...   

   has_swf_in_string  has_cgi_in_string  has_php_in_string  \
0                  0                  0                  0   
1                  0                  0                  0   
2                  0                  0                  0   
3                  0                  0                  1   
4                  0                  0                  1   

   has_abuse_in_string  has_admin_in_string  has_bin_in_string  \
0                    0                    0                  0   
1                    0                    0                  0   
2                    0                    0                  0   
3                    0                    0                  0   
4                    0                    0                  0   

   has_personal_in_string  has_update_in_string  has_verification_in_string  \
0                       0                     0                           0   
1                       0                     0                           0   
2                       0                     0                           0   
3                       0                     0                           0   
4                       0                     0                           0   

   url_scheme  
0           0  
1           0  
2           0  
3          27  
4          27  

[5 rows x 77 columns]

##### Upsampling

In [2]:
from sklearn.utils import resample

dataset_benign = dataset[(dataset['url_type'] == 0)]
dataset_malicious = dataset[(dataset['url_type'] == 1)]

dataset_malicious_upsampled = resample(dataset_malicious,
                                        replace=True,
                                        n_samples = dataset_benign.shape[0],
                                        random_state = 15)

dataset_upsampled = pd.concat([dataset_benign, dataset_malicious_upsampled])

dataset_upsampled['url_type'].value_counts()

url_type
0    724778
1    724778
Name: count, dtype: int64

##### Setting the Variables

In [3]:
x_train, x_test, y_train, y_test = train_test_split(dataset_upsampled.drop(columns=['url_type']), dataset_upsampled['url_type'], test_size = 0.2, random_state=42)

In [4]:
valid = pd.read_csv("../../../02_feature-engineering/final-datasets/valid_unbalanced_with_lexical.csv")
valid.head()

y_valid = valid['url_type']
X_valid = valid.drop(columns=['url_type'])

#### 2. Preprocessing (Balancing)

In [5]:
dataset_upsampled['url_type'].value_counts()

url_type
0    724778
1    724778
Name: count, dtype: int64

#### 3. Removing Unnecessary Features

In [6]:
important_features_wrapper_33 = ['url_length',
 'url_domain_entropy',
 'url_is_digits_in_domain',
 'url_number_of_parameters',
 'url_number_of_digits',
 'url_string_entropy',
 'url_path_length',
 'url_host_length',
 'url_domain_len',
 'url_num_subdomain',
 'url_number_of_fragments',
 'url_is_encoded',
 'url_number_of_letters',
 'url_num_periods',
 'url_num_of_hyphens',
 'url_num_underscore',
 'url_num_forward_slash',
 'url_num_semicolon',
 'url_num_mod_sign',
 'has_login_in_string',
 'has_signin_in_string',
 'has_logon_in_string',
 'has_loginasp_in_string',
 'has_exe_in_string',
 'has_viewerphp_in_string',
 'has_getImageasp_in_string',
 'has_paypal_in_string',
 'has_dbsysphp_in_string',
 'has_shopping_in_string',
 'has_php_in_string',
 'has_bin_in_string',
 'has_personal_in_string'
 ]

important_features_wrapper_12 = ['url_domain_entropy', 
                              'url_number_of_parameters', 
                              'url_number_of_digits', 
                              'url_path_length', 
                              'url_host_length', 
                              'get_tld', 
                              'url_domain_len', 
                              'url_num_subdomain', 
                              'url_number_of_letters', 
                              'url_num_periods', 
                              'url_num_of_hyphens', 
                              'url_num_forward_slash', 
                              'url_num_semicolon', 
                              'has_login_in_string', 
                              'has_exe_in_string', 
                              'has_php_in_string', 
                              'url_scheme']

X_test_12 = x_test[important_features_wrapper_12]
X_train_12 = x_train[important_features_wrapper_12]

X_test_33 = x_test[important_features_wrapper_33]
X_train_33 = x_train[important_features_wrapper_33]
X_valid_33 = X_valid[important_features_wrapper_33]

X_test_33.head()

url_length  url_domain_entropy  url_is_digits_in_domain  \
661297           30            3.180833                        1   
111085           86            2.646439                        0   
76453            40            2.947703                        0   
626549           26            2.235926                        0   
1024969          64            3.189898                        0   

         url_number_of_parameters  url_number_of_digits  url_string_entropy  \
661297                          0                     3            3.989898   
111085                          0                     8            4.500953   
76453                           0                     6            4.239823   
626549                          0                     0            3.642371   
1024969                         0                     0            4.247578   

         url_path_length  url_host_length  url_domain_len  url_num_subdomain  \
661297                30                0              13                  1   
111085                65               14              10                  1   
76453                 40                0               9                  1   
626549                26                0               7                  1   
1024969               35               22              15                  1   

         ...  has_loginasp_in_string  has_exe_in_string  \
661297   ...                       0                  0   
111085   ...                       0                  0   
76453    ...                       0                  0   
626549   ...                       0                  0   
1024969  ...                       0                  0   

         has_viewerphp_in_string  has_getImageasp_in_string  \
661297                         0                          0   
111085                         0                          0   
76453                          0                          0   
626549                         0                          0   
1024969                        0                          0   

         has_paypal_in_string  has_dbsysphp_in_string  has_shopping_in_string  \
661297                      0                       0                       0   
111085                      0                       0                       0   
76453                       0                       0                       0   
626549                      0                       0                       0   
1024969                     0                       0                       0   

         has_php_in_string  has_bin_in_string  has_personal_in_string  
661297                   0                  0                       0  
111085                   0                  0                       0  
76453                    0                  0                       0  
626549                   0                  0                       0  
1024969                  1                  0                       0  

[5 rows x 32 columns]

#### Hyper-parameter Tuning

##### 12 Features (Purely Lexical)

In [7]:
import optuna
from sklearn.metrics import mean_squared_error # or any other metric
from sklearn.model_selection import train_test_split

# Define the objective function for Optuna
'''def objective_12(trial):
    # Define the search space for hyperparameters
    param = {
        'objective': 'binary:hinge',
        'eval_metric': 'error',
        'eta': trial.suggest_float('eta', 0.01, 0.3),
        'n_estimators': 100000, # Fix the boosting round and use early stopping
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_float('gamma', 0.0, 10.0),
        'min_child_weight': trial.suggest_float('min_child_weight', 0.1, 10.0),
        'lambda': trial.suggest_float('lambda', 0.1, 10.0),
        'alpha': trial.suggest_float('alpha', 0.0, 10.0),
    }
    
    # Split the data into further training and validation sets (three sets are preferable)
    train_data, valid_data, train_target, valid_target = train_test_split(X_train_12, y_train, test_size=0.2, random_state=42)
    
    # Convert the data into DMatrix format
    dtrain = DMatrix(train_data, label=train_target)
    dvalid = DMatrix(valid_data, label=valid_target)
    
    # Define the pruning callback for early stopping
    pruning_callback = optuna.integration.XGBoostPruningCallback(trial, 'validation-error')
    
    # Train the model with early stopping
    model = train(param, dtrain, num_boost_round=100000, evals=[(dvalid, 'validation')], early_stopping_rounds=100, callbacks=[pruning_callback])
    
    # Make predictions on the test set
    dtest = DMatrix(valid_data)
    y_pred = model.predict(dtest)
    
    # Calculate the root mean squared error
    error = mean_squared_error(valid_target, y_pred, squared=False)
    
    return error

# Create an Optuna study and optimize the objective function
study_12 = optuna.create_study(direction='minimize')
study_12.optimize(objective_12, n_trials=100) # Control the number of trials

# Print the best hyperparameters and the best RMSE
best_params_12 = study_12.best_params
best_error = study_12.best_value
print("Best Hyperparameters (12 Features): ", best_params_12)
print("Best Error (12 Features): ", best_error)'''

c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


'def objective_12(trial):\n    # Define the search space for hyperparameters\n    param = {\n        \'objective\': \'binary:hinge\',\n        \'eval_metric\': \'error\',\n        \'eta\': trial.suggest_float(\'eta\', 0.01, 0.3),\n        \'n_estimators\': 100000, # Fix the boosting round and use early stopping\n        \'max_depth\': trial.suggest_int(\'max_depth\', 3, 10),\n        \'subsample\': trial.suggest_float(\'subsample\', 0.5, 1.0),\n        \'colsample_bytree\': trial.suggest_float(\'colsample_bytree\', 0.5, 1.0),\n        \'gamma\': trial.suggest_float(\'gamma\', 0.0, 10.0),\n        \'min_child_weight\': trial.suggest_float(\'min_child_weight\', 0.1, 10.0),\n        \'lambda\': trial.suggest_float(\'lambda\', 0.1, 10.0),\n        \'alpha\': trial.suggest_float(\'alpha\', 0.0, 10.0),\n    }\n    \n    # Split the data into further training and validation sets (three sets are preferable)\n    train_data, valid_data, train_target, valid_target = train_test_split(X_train_12, 

##### 33 Features (Purely Lexical)

In [8]:
# Define the objective function for Optuna
def objective_33(trial):
    # Define the search space for hyperparameters
    param = {
        'objective': 'binary:hinge',
        'eval_metric': 'error',
        'eta': trial.suggest_float('eta', 0.01, 0.3),
        'n_estimators': 100000, # Fix the boosting round and use early stopping
        'max_depth': trial.suggest_int('max_depth', 3, 10),
        'subsample': trial.suggest_float('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'gamma': trial.suggest_float('gamma', 0.0, 10.0),
        'min_child_weight': trial.suggest_float('min_child_weight', 0.1, 10.0),
        'lambda': trial.suggest_float('lambda', 0.1, 10.0),
        'alpha': trial.suggest_float('alpha', 0.0, 10.0),
    }
    
    # Split the data into further training and validation sets (three sets are preferable)
    train_data, valid_data, train_target, valid_target = train_test_split(X_train_33, y_train, test_size=0.2, random_state=42)
    
    # Convert the data into DMatrix format
    dtrain = DMatrix(train_data, label=train_target)
    dvalid = DMatrix(valid_data, label=valid_target)
    
    # Define the pruning callback for early stopping
    pruning_callback = optuna.integration.XGBoostPruningCallback(trial, 'validation-error')
    
    # Train the model with early stopping
    model = train(param, dtrain, num_boost_round=100000, evals=[(dvalid, 'validation')], early_stopping_rounds=100, callbacks=[pruning_callback])
    
    # Make predictions on the test set
    dtest = DMatrix(valid_data)
    y_pred = model.predict(dtest)
    
    # Calculate the root mean squared error
    error = mean_squared_error(valid_target, y_pred, squared=False)
    
    return error

# Create an Optuna study and optimize the objective function
study_33 = optuna.create_study(direction='minimize')
optuna.logging.disable_propagation
study_33.optimize(objective_33, n_trials=100) # Control the number of trials

# Print the best hyperparameters and the best RMSE
best_params_33 = study_33.best_params
best_error_33 = study_33.best_value
print("Best Hyperparameters (33 Features): ", best_params_33)
print("Best Error (33 Features): ", best_error_33)

[I 2024-05-14 12:46:17,008] A new study created in memory with name: no-name-8d750db0-1caf-4754-880d-1fc6f5721820
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\xgboost\core.py:160: UserWarning: [12:46:18] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-07f6e447eee219473-1\xgboost\xgboost-ci-windows\src\learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


[0]	validation-error:0.50227
[1]	validation-error:0.50227
[2]	validation-error:0.50227
[3]	validation-error:0.50227
[4]	validation-error:0.50227
[5]	validation-error:0.50227
[6]	validation-error:0.50227
[7]	validation-error:0.50227
[8]	validation-error:0.50227
[9]	validation-error:0.48664
[10]	validation-error:0.46240
[11]	validation-error:0.45648
[12]	validation-error:0.42441
[13]	validation-error:0.40134
[14]	validation-error:0.38199
[15]	validation-error:0.36839
[16]	validation-error:0.35118
[17]	validation-error:0.33342
[18]	validation-error:0.31623
[19]	validation-error:0.30439
[20]	validation-error:0.29659
[21]	validation-error:0.28911
[22]	validation-error:0.27734
[23]	validation-error:0.26083
[24]	validation-error:0.24455
[25]	validation-error:0.24010
[26]	validation-error:0.23429
[27]	validation-error:0.22791
[28]	validation-error:0.22239
[29]	validation-error:0.21777
[30]	validation-error:0.21237
[31]	validation-error:0.20972
[32]	validation-error:0.20662
[33]	validation-erro

[I 2024-05-14 12:52:00,216] Trial 0 finished with value: 0.24491605577288644 and parameters: {'eta': 0.06776168994772483, 'max_depth': 5, 'subsample': 0.5438865250762456, 'colsample_bytree': 0.6430749929507613, 'gamma': 2.2359922054999926, 'min_child_weight': 2.9550574971672967, 'lambda': 0.7879885934452795, 'alpha': 9.79117795496187}. Best is trial 0 with value: 0.24491605577288644.
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\xgboost\core.py:160: UserWarning: [12:52:01] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-07f6e447eee219473-1\xgboost\xgboost-ci-windows\src\learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


[0]	validation-error:0.50227
[1]	validation-error:0.50227
[2]	validation-error:0.50227
[3]	validation-error:0.50227
[4]	validation-error:0.50227
[5]	validation-error:0.50227
[6]	validation-error:0.50227
[7]	validation-error:0.50227
[8]	validation-error:0.50227
[9]	validation-error:0.50227
[10]	validation-error:0.50227
[11]	validation-error:0.50227
[12]	validation-error:0.50227
[13]	validation-error:0.50227
[14]	validation-error:0.50227
[15]	validation-error:0.50227
[16]	validation-error:0.50227
[17]	validation-error:0.50227
[18]	validation-error:0.50227
[19]	validation-error:0.50227
[20]	validation-error:0.50227
[21]	validation-error:0.50227
[22]	validation-error:0.50227
[23]	validation-error:0.50227
[24]	validation-error:0.50227
[25]	validation-error:0.50227
[26]	validation-error:0.50227
[27]	validation-error:0.50227
[28]	validation-error:0.50227
[29]	validation-error:0.50227
[30]	validation-error:0.50227
[31]	validation-error:0.50227
[32]	validation-error:0.50227
[33]	validation-erro

[I 2024-05-14 12:53:46,546] Trial 1 finished with value: 0.26433848070995747 and parameters: {'eta': 0.015465779260014682, 'max_depth': 10, 'subsample': 0.9312100352097552, 'colsample_bytree': 0.514022280527425, 'gamma': 6.868132829754536, 'min_child_weight': 2.5376181448312587, 'lambda': 0.46512994114829753, 'alpha': 4.167079832091703}. Best is trial 0 with value: 0.24491605577288644.
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\xgboost\core.py:160: UserWarning: [12:53:47] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-07f6e447eee219473-1\xgboost\xgboost-ci-windows\src\learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


...

[0]	validation-error:0.50227
[1]	validation-error:0.37457
[2]	validation-error:0.20450
[3]	validation-error:0.18970
[4]	validation-error:0.17565
[5]	validation-error:0.16605
[6]	validation-error:0.15732
[7]	validation-error:0.14929
[8]	validation-error:0.13528
[9]	validation-error:0.13153
[10]	validation-error:0.12374
[11]	validation-error:0.12014
[12]	validation-error:0.11501
[13]	validation-error:0.11149
[14]	validation-error:0.10830
[15]	validation-error:0.10634
[16]	validation-error:0.10333
[17]	validation-error:0.10119
[18]	validation-error:0.09880
[19]	validation-error:0.09629
[20]	validation-error:0.09311
[21]	validation-error:0.09167
[22]	validation-error:0.09115
[23]	validation-error:0.09019
[24]	validation-error:0.08791
[25]	validation-error:0.08682
[26]	validation-error:0.08618
[27]	validation-error:0.08522
[28]	validation-error:0.08452
[29]	validation-error:0.08378
[30]	validation-error:0.08346
[31]	validation-error:0.08273
[32]	validation-error:0.08263
[33]	validation-erro

[I 2024-05-14 15:28:26,966] Trial 98 finished with value: 0.18617591056285673 and parameters: {'eta': 0.2659297978432621, 'max_depth': 10, 'subsample': 0.5157965754567595, 'colsample_bytree': 0.9501635400813253, 'gamma': 1.5623252735386166, 'min_child_weight': 6.539756678512535, 'lambda': 5.927754246782471, 'alpha': 8.274485782618779}. Best is trial 86 with value: 0.17976630460107768.
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\xgboost\core.py:160: UserWarning: [15:28:27] WARNING: C:\buildkite-agent\builds\buildkite-windows-cpu-autoscaling-group-i-07f6e447eee219473-1\xgboost\xgboost-ci-windows\src\learner.cc:742: 
Parameters: { "n_estimators" } are not used.

  warnings.warn(smsg, UserWarning)


[0]	validation-error:0.50227
[1]	validation-error:0.35096
[2]	validation-error:0.20123
[3]	validation-error:0.18833
[4]	validation-error:0.16792
[5]	validation-error:0.15995
[6]	validation-error:0.14914
[7]	validation-error:0.13473
[8]	validation-error:0.13140
[9]	validation-error:0.12715
[10]	validation-error:0.12160
[11]	validation-error:0.11801
[12]	validation-error:0.11520
[13]	validation-error:0.11353
[14]	validation-error:0.11151
[15]	validation-error:0.10841
[16]	validation-error:0.10545
[17]	validation-error:0.10251
[18]	validation-error:0.10054
[19]	validation-error:0.09764
[20]	validation-error:0.09536
[21]	validation-error:0.09397
[22]	validation-error:0.09277
[23]	validation-error:0.09098
[24]	validation-error:0.08831
[25]	validation-error:0.08726
[26]	validation-error:0.08643
[27]	validation-error:0.08548
[28]	validation-error:0.08461
[29]	validation-error:0.08383
[30]	validation-error:0.08343
[31]	validation-error:0.08302
[32]	validation-error:0.08280
[33]	validation-erro

[I 2024-05-14 15:31:03,158] Trial 99 finished with value: 0.18828304291450468 and parameters: {'eta': 0.27279106566399886, 'max_depth': 10, 'subsample': 0.5400288930759456, 'colsample_bytree': 0.9657329382868222, 'gamma': 1.847722362307907, 'min_child_weight': 5.399476063873799, 'lambda': 7.316015096023789, 'alpha': 8.024392147161906}. Best is trial 86 with value: 0.17976630460107768.


Best Hyperparameters (33 Features):  {'eta': 0.29332986924987164, 'max_depth': 10, 'subsample': 0.503875472477248, 'colsample_bytree': 0.8477742131948753, 'gamma': 0.7797982719809899, 'min_child_weight': 5.935950151663066, 'lambda': 4.63767788955845, 'alpha': 8.428871872314394}
Best Error (33 Features):  0.17976630460107768


In [9]:
# print(best_params_12)
print(best_params_33)

{'eta': 0.29332986924987164, 'max_depth': 10, 'subsample': 0.503875472477248, 'colsample_bytree': 0.8477742131948753, 'gamma': 0.7797982719809899, 'min_child_weight': 5.935950151663066, 'lambda': 4.63767788955845, 'alpha': 8.428871872314394}


#### Model Training

In [10]:
from sklearn.model_selection import KFold
import optuna

# Initialize CV
cv = KFold(n_splits=10, shuffle=True, random_state=1)

# best_params_12['objective'] = 'binary:hinge'
# best_params_12['eval_metric'] = 'error'

best_params_33['objective'] = 'binary:hinge'
best_params_33['eval_metric'] = 'error'

# Convert the data into DMatrix format
# dtrain_12 = DMatrix(X_train_12, label=y_train)
# dvalid_12 = DMatrix(X_test_12, label=y_test)

dtrain_33 = DMatrix(X_train_33, label=y_train)
dvalid_33 = DMatrix(X_test_33, label=y_test)
lexical_valid = DMatrix(X_valid_33, label = y_valid)

# Train the Model
# xgb_classifier_12 = train(best_params_12, dtrain_12, num_boost_round=3000)
# y_pred_12 = xgb_classifier_12.predict(dvalid_12)

# print("Model with 12 Features Done.")

xgb_classifier_33 = train(best_params_33, dtrain_33, num_boost_round=3000)
y_pred_33 = xgb_classifier_33.predict(dvalid_33)
y_pred_valid = xgb_classifier_33.predict(lexical_valid)

print("Model with 33 Features Done.")

Model with 33 Features Done.


In [11]:
# Exporting some stuff for concept drift

# Actual Values
y_test.to_csv("warm-up-actual.csv", encoding='utf-8', index=False)
y_valid.to_csv("testing-actual.csv", encoding='utf-8', index=False)

temp_pred_test = pd.DataFrame(y_pred_33)
temp_pred_valid = pd.DataFrame(y_pred_valid)

temp_pred_test.to_csv("warm-up-predicted.csv", encoding='utf-8', index=False)
temp_pred_valid.to_csv("testing-predicted.csv", encoding='utf-8', index=False)

#### Evaluation

In [12]:
# Classification Report
print("------------- Test Evaluation -------------")
# print(classification_report(y_test, y_pred_12))
print(classification_report(y_test, y_pred_33))

------------- Test Evaluation -------------
              precision    recall  f1-score   support

           0       0.98      0.96      0.97    144676
           1       0.96      0.98      0.97    145236

    accuracy                           0.97    289912
   macro avg       0.97      0.97      0.97    289912
weighted avg       0.97      0.97      0.97    289912



In [13]:
# Classification Report
print("------------- Practical Evaluation -------------")

print(classification_report(y_valid, y_pred_valid))

------------- Practical Evaluation -------------
              precision    recall  f1-score   support

         0.0       1.00      0.00      0.01      1000
         1.0       0.00      0.00      0.00         0

    accuracy                           0.00      1000
   macro avg       0.50      0.00      0.00      1000
weighted avg       1.00      0.00      0.01      1000



c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\sison\AppData\Local\Programs\Python\Python311\Lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Recall and F-score are ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, le

In [14]:
'''# Confusion Matrix for 12 Features
cm_up = confusion_matrix(y_test, y_pred_12, labels=xgb_classifier_12.classes_)
disp = ConfusionMatrixDisplay(confusion_matrix = cm_up, display_labels = xgb_classifier_12.classes_)
disp.plot()
plt.show()'''

'# Confusion Matrix for 12 Features\ncm_up = confusion_matrix(y_test, y_pred_12, labels=xgb_classifier_12.classes_)\ndisp = ConfusionMatrixDisplay(confusion_matrix = cm_up, display_labels = xgb_classifier_12.classes_)\ndisp.plot()\nplt.show()'

In [15]:
'''# Cross Validation Score
scores = cross_val_score(XGBClassifier(**params_gbm),
                        X_train, y_train, scoring='accuracy', cv=cv).mean()

print(scores)'''

"# Cross Validation Score\nscores = cross_val_score(XGBClassifier(**params_gbm),\n                        X_train, y_train, scoring='accuracy', cv=cv).mean()\n\nprint(scores)"

In [16]:
# Dumping the model
# joblib.dump(xgb_classifier_12, 'xgb_ffs_12.sav')
joblib.dump(xgb_classifier_33, 'xgb_wrapper_31_lexical.sav')

['xgb_wrapper_31_lexical.sav']

In [26]:
import lexical_generator_12
import lexical_generator_33
import time

'''def xgb_predict_maliciousness_12(url):

    numerical_values = lexical_generator_12.lexical_generator(url)
    # print(numerical_values)
    numerical_values = DMatrix(numerical_values)

    match xgb_classifier_12.predict(numerical_values):
        case 0:
            return "Benign"
        case 1:
            return "Malware"
        case 2:
            return "Phishing"
        case 3:
            return "Defacement"'''
        
def xgb_predict_maliciousness_33(url):

    numerical_values = lexical_generator_33.lexical_generator(url)
    # print(numerical_values)
    numerical_values = DMatrix(numerical_values)

    match xgb_classifier_33.predict(numerical_values):
        case 0:
            return "Benign"
        case 1:
            return "Malware"
        case 2:
            return "Phishing"
        case 3:
            return "Defacement"

url = "https://www.facebook.com/messages/t/7618975898128964"
print("Current URL: "+url)

'''print("------------- Wrapper-Based (12 Features) -------------")
for i in range(15):
    start = time.perf_counter()
    prediction = xgb_predict_maliciousness_12(url)
    end = time.perf_counter()
    print("Trial "+str(i))
    print(prediction)
    print(end-start)'''

print("------------- Wrapper-Based (33 Features) -------------")
for i in range(1):
    start = time.perf_counter()
    prediction = xgb_predict_maliciousness_33(url)
    end = time.perf_counter()
    print("Trial "+str(i))
    print(prediction)
    print(end-start)

Current URL: https://www.facebook.com/messages/t/7618975898128964
------------- Wrapper-Based (33 Features) -------------
Trial 0
Benign
0.012987599999178201
